# Assignment

In [4]:
# Import 

import numpy as np
import matplotlib.pyplot as plt
import numpy.matlib
import pandas as pd
from degree_freedom_queen import *
from degree_freedom_king1 import *
from degree_freedom_king2 import *
from generate_game import *
from Chess_env import *
import random

size_board = 4
## INITIALISE THE ENVIRONMENT

env=Chess_Env(size_board)

## The Environment

You can find the environment in the file Chess_env, which contains the class Chess_env. To define an object, you need to provide the board size considered as input. In our example, size_board=4. 
Chess_env is composed by the following methods:

1. Initialise_game. The method initialises an episode by placing the three pieces considered (Agent's king and queen, enemy's king) in the chess board. The outputs of the method are described below in order.

     S $\;$ A matrix representing the board locations filled with 4 numbers: 0, no piece in that position; 1, location of the 
     agent's king; 2 location of the queen; 3 location of the enemy king.
     
     X $\;$ The features, that is the input to the neural network. See the assignment for more information regarding the            definition of the features adopted. To personalise this, go into the Features method of the class Chess_env() and change        accordingly.
     
     allowed_a $\;$ The allowed actions that the agent can make. The agent is moving a king, with a total number of 8                possible actions, and a queen, with a total number of $(board_{size}-1)\times 8$ actions. The total number of possible actions correspond      to the sum of the two, but not all actions are allowed in a given position (movements to locations outside the borders or      against chess rules). Thus, the variable allowed_a is a vector that is one (zero) for an action that the agent can (can't)      make. Be careful, apply the policy considered on the actions that are allowed only.
     

2. OneStep. The method performs a one step update of the system. Given as input the action selected by the agent, it updates the chess board by performing that action and the response of the enemy king (which is a random allowed action in the settings considered). The first three outputs are the same as for the Initialise_game method, but the variables are computed for the position reached after the update of the system. The fourth and fifth outputs are:

     R $\;$ The reward. To change this, look at the OneStep method of the class where the rewards are set.
     
     Done $\;$ A variable that is 1 if the episode has ended (checkmate or draw).
     
     
3. Features. Given the chessboard position, the method computes the features.

This information and a quick analysis of the class should be all you need to get going. The other functions that the class exploits are uncommented and constitute an example on how not to write a python code. You can take a look at them if you want, but it is not necessary.






In [10]:
##  Define functions

def EpsilonGreedy_Policy(Qvalues, epsilon, allowed_a):
    
    N_a=np.shape(Qvalues)[0]
    a = list(range(0, N_a))
    a = [i for idx, i in enumerate(a) if allowed_a[idx]]
    Qvalues = [i for idx, i in enumerate(Qvalues) if allowed_a[idx]]

    rand_value=np.random.uniform(0,1)
 ## epsilon is probability that we go random
    rand_a=rand_value<epsilon

    if rand_a==True:
        
        a = random.choice(a)

    else:
        idx=np.argmax(Qvalues)
        a = a[idx]
            
    return a


def ComputeQvalues(W1, W2, bias_W1, bias_W2, X, hiddenactivfunction , outeractivfunction):
    ## Qvalues=np.matmul(W2, np.matmul(W1,X)) ## this is direct computation of hidden layer and then output layer, without applying any non linear activation function
    ## below is a better solution:
    # Neural activation: input layer -> hidden layer
    H1 = np.matmul(W1,X)+bias_W1 ## make sure that bias_W1 does not need to be transposed
    # if hidden activ function is given:
    if (hiddenactivfunction == 1):
        H1 = np.round(1/(1+np.exp(-H1)), 5)
        
    Qvalues = np.matmul(W2,H1) + bias_W2
    
    #if outer activ function is given
    if (outeractivfunction == 1):
        Qvalues = np.round(1/(1+np.exp(- Qvalues)), 5)

    return Qvalues

In [26]:
# INITIALISE THE PARAMETERS OF YOUR NEURAL NETWORK AND...
# PLEASE CONSIDER TO USE A MASK OF ONE FOR THE ACTION MADE AND ZERO OTHERWISE IF YOU ARE NOT USING VANILLA GRADIENT DESCENT...
# WE SUGGEST A NETWORK WITH ONE HIDDEN LAYER WITH SIZE 200. 


S,X,allowed_a=env.Initialise_game()



N_a=np.shape(allowed_a)[0]   # TOTAL NUMBER OF POSSIBLE ACTIONS
N_in=np.shape(X)[0]    ## INPUT SIZE
N_h=200                ## NUMBER OF HIDDEN NODES



## INITALISE YOUR NEURAL NETWORK... Here weights from input to hidden layer and from the hidden layer to output layer are initialized
W1=np.random.randn(N_h,N_in)/1000
W2=np.random.randn(N_a,N_h)/1000


##W1 = np.divide(W1,np.matlib.repmat(np.sum(W1,1)[:,None],1,N_in))
##W2 = np.divide(W2,np.matlib.repmat(np.sum(W2,1)[:,None],1,N_h))


bias_W1 = np.zeros((N_h,))

bias_W2 = np.zeros((N_a,))



# HYPERPARAMETERS SUGGESTED (FOR A GRID SIZE OF 4)

epsilon_0 = 0.8     # STARTING VALUE OF EPSILON FOR THE EPSILON-GREEDY POLICY
beta = 0.05      # THE PARAMETER SETS HOW QUICKLY THE VALUE OF EPSILON IS DECAYING (SEE epsilon_f BELOW)
gamma = 0.85        # THE DISCOUNT FACTOR
eta = 0.0035        # THE LEARNING RATE

N_episodes = 1000 # THE NUMBER OF GAMES TO BE PLAYED 

hiddenactivfunction = 0
outeractivfunction = 0

# SAVING VARIABLES
R_save = np.zeros([N_episodes, 1])
N_moves_save = np.zeros([N_episodes, 1])


In [ ]:
# SARSA

for n in range(N_episodes):
    S,X,allowed_a=env.Initialise_game()
   
    epsilon_f = epsilon_0 / (1 + beta * n)   ## DECAYING EPSILON
    Done=0                                   ## SET DONE TO ZERO (BEGINNING OF THE EPISODE)
    i = 1                                    ## COUNTER FOR NUMBER OF ACTIONS
                               
    Qvalues = ComputeQvalues(W1, W2, bias_W1, bias_W2, X, hiddenactivfunction , outeractivfunction)

    
    a=EpsilonGreedy_Policy(Qvalues,epsilon_f, allowed_a)
    
    while (Done==0 and i<50):                           ## START THE EPISODE
       
        Qvalues = ComputeQvalues(W1, W2, bias_W1, bias_W2, X, hiddenactivfunction , outeractivfunction)   
        print(Qvalues)
        S_next, X_next,allowed_a_next,R,Done=env.OneStep(a)
        
        ## THE EPISODE HAS ENDED, UPDATE...BE CAREFUL, THIS IS THE LAST STEP OF THE EPISODE
        if Done==1:
            R_save[n,]=np.copy(R)
            #print(i)
            N_moves_save[n,]=i
           
          
             ## update W2 and B2   
            dEdQ=R-Qvalues[a]
            dQdY = 1  
            if outeractivfunction == 1:
                    dQdY = Qvalues[a]*(1-Qvalues[a])
                    
          
            H = np.matmul(W1,X) + bias_W1
            if hiddenactivfunction == 1:
                     H = np.round(1/(1+np.exp(-H)), 5)
            dYdW = H

        
            W2[a,:]=W2[a,:]+eta*dEdQ*dQdY*dYdW
            bias_W2[a]=bias_W2[a]+eta*dEdQ*dQdY
            
            
             ## update W1 and B1 after W2 and B2 were updated
            
            
            dYdZ =  W2[a,:].reshape(200, 1)
            if hiddenactivfunction == 1:
                dYdZ = np.multiply(dYdZ, H*(1-H))
        
                        
            W1[:,:]=W1[:,:]+ eta*dEdQ*dQdY*dYdZ*dZDW 
            bias_W1=bias_W1+eta*dEdQ*dQdY*dYdZ.reshape(200,)  
            
            break
        
       
  
        
        
        # IF THE EPISODE IS NOT OVER...
        else:
            
            Qvalues1=ComputeQvalues(W1, W2, bias_W1, bias_W2, X_next, hiddenactivfunction , outeractivfunction)
            
            a1=EpsilonGreedy_Policy(Qvalues1,epsilon_f, allowed_a_next)

            # Compute the delta
         
            
            delta=R+gamma*1- Qvalues1[a1]- Qvalues[a]

            # Update the weights
    
            R_save[n,]=np.copy(R)
            #print(i)
            N_moves_save[n,]=i
           
          
             ## update W2 and B2   
            dEdQ=R-Qvalues[a]
            dQdY = 1  
            if outeractivfunction == 1:
                    dYdQ = Qvalues[a]*(1-Qvalues[a])
                    
          
            H = np.matmul(W1,X) + bias_W1
            if hiddenactivfunction == 1:
                     H = np.round(1/(1+np.exp(-H)), 5)
            dYdW = H
    
        
            W2[a,:]=W2[a,:]+eta*dEdQ*dQdY*dYdW
            bias_W2[a]=bias_W2[a]+eta*dEdQ*dQdY
            
            
             ## update W1 and B1 after W2 and B2 were updated
            
            
            dYdZ =  W2[a,:].reshape(200, 1)
            if hiddenactivfunction == 1:
                dYdZ = np.multiply(dYdZ, H*(1-H))
        
            dZDW = X.reshape(1, 58)        
            W1[:,:]=W1[:,:]+ eta*dEdQ*dQdY*dYdZ*dZDW 
            bias_W1=bias_W1+ eta*dEdQ*dQdY*dYdZ.reshape(200,) 
            
        # NEXT STATE AND CO. BECOME ACTUAL STATE...     
        S=np.copy(S_next)
        X=np.copy(X_next)
        a = np.copy(a1)

        i += 1  # UPDATE COUNTER FOR NUMBER OF ACTIONS

        
        
    
    

[-4.17675065e-05 -1.02429918e-05  3.34472548e-05 -4.35535517e-05
 -2.02900315e-06 -2.21009964e-05 -9.25596133e-06  3.02708291e-05
  2.61093411e-05  1.74335846e-05 -1.53780381e-05 -7.94326852e-06
 -5.32328108e-06  1.15598514e-05 -3.59832358e-05 -3.93019455e-05
 -8.25859713e-06 -3.17044100e-05  5.85783586e-05 -3.33325276e-06
 -2.56558274e-05  5.35366688e-05 -2.36580927e-05  1.51561398e-05
  5.19440694e-05  1.31835847e-05  1.96173479e-05  1.94150825e-05
  1.10318695e-06  5.50898957e-06  3.97104026e-06  5.13020333e-07]
[-2.46175486e-05 -5.84990288e-05 -2.47538421e-07 -3.44585566e-05
 -2.04855306e-06 -2.28545804e-05 -2.04699042e-05  8.27718410e-06
 -4.81069522e-05 -2.25717510e-06  9.89453616e-06 -5.79608463e-06
  2.92815909e-05  6.13869465e-05 -5.12052819e-05 -2.07667690e-05
 -1.71312401e-06  1.78288420e-05  2.71012085e-05 -2.75866053e-06
  6.21578074e-06  3.78718730e-05 -3.89220791e-05 -2.28579665e-05
  1.72495874e-05  2.52195079e-05  6.78615634e-06  8.25586681e-05
  6.20396948e-05 -1.5806

[-5.16582297e-05  5.27628840e-05  3.51356069e-03 -6.40127595e-05
  3.07948095e-05 -9.82877166e-06  3.47273390e-03  5.30963520e-05
  3.08979965e-05  4.12647435e-05  3.57814384e-05  3.53480954e-05
 -1.18059750e-05  2.07393926e-05 -4.72350002e-06  1.65702941e-05
 -3.65847858e-05 -8.46157977e-05 -1.14989427e-05 -2.95552469e-06
  8.30582308e-06  6.03251551e-05 -1.65484169e-05 -1.37206476e-05
 -1.36128098e-05 -4.80519492e-06  7.08948106e-07  1.96784506e-05
  2.41955002e-05 -1.35374465e-06  3.32942308e-05 -3.96481680e-06]
[-2.24643066e-05 -6.58349730e-06  3.56373598e-03 -4.07176140e-05
  1.19088063e-05 -1.58903381e-05  3.46220865e-03  2.76029328e-05
 -1.60998655e-05 -3.23662038e-05  1.04189503e-05  1.67522723e-06
 -5.21468237e-05  2.20229926e-06 -2.60284557e-05  1.75957805e-05
 -3.83358611e-05  1.46444487e-05  1.80268396e-05  1.92928145e-05
  3.05286633e-05  5.57821845e-05 -2.72704904e-05 -5.85850890e-06
  9.22057836e-06 -1.99847515e-05 -1.13291128e-05 -6.13149153e-07
  5.54844214e-05  1.6682

[-2.85242150e-05 -1.47723293e-05  3.47851610e-03 -3.09153691e-05
 -2.02741260e-05 -1.07567199e-05  3.30591396e-03  8.08623292e-05
 -2.44020566e-05 -2.50567693e-06 -1.42831564e-05  1.63843237e-05
  9.02484319e-06  3.62016336e-05 -6.01025573e-05 -5.34640372e-05
 -3.65951983e-05 -3.17787807e-05  6.10479424e-06 -6.42097539e-06
  4.05701729e-05  3.14618757e-05  4.14470859e-06 -1.37892042e-05
  3.64786172e-05  2.70597616e-05  2.73033072e-05  4.22015914e-05
  3.57866618e-05  2.08391256e-05  3.30566943e-06 -3.68194804e-05]
[-1.51845255e-05 -1.76079887e-05  3.50562997e-03 -4.80672986e-05
  2.70600301e-05  4.23076840e-06  3.32753609e-03 -9.98481319e-06
  1.55569370e-05 -1.14708876e-06  1.30151807e-05 -9.68177105e-06
 -2.42437770e-05 -6.59430512e-06 -2.23369191e-05  7.28125227e-06
  1.54805044e-05 -5.81921457e-05  1.75611422e-05  2.33732382e-05
 -3.54996239e-05  3.98180347e-05 -1.27050128e-05  1.20105190e-05
  5.24012985e-05  1.22671096e-05  3.85490706e-05  7.75012760e-07
 -5.41171058e-06  7.3860

[ 1.48357108e-05  3.42371172e-03  3.47314582e-03  2.68952897e-05
 -1.21956156e-05 -3.49541014e-05  3.07391974e-03  9.16762094e-06
 -2.93839741e-05 -4.09897371e-05  1.83492312e-06 -3.82330432e-05
 -3.95982964e-05  5.65249758e-05  1.06641851e-05  1.92412722e-05
  3.48163046e-03  1.40116582e-05 -1.01255643e-05 -2.36582916e-05
 -2.61460699e-05  6.39907485e-05 -5.17615970e-05 -3.38800697e-06
  5.94176145e-05  1.05884744e-05  1.98995316e-05  4.05216649e-05
  1.76242256e-05 -1.88190834e-05 -2.70922397e-05 -1.24071220e-05]
[ 3.74884272e-05  3.43302318e-03  3.48138613e-03 -1.19903797e-05
 -4.31076978e-05 -2.88322976e-05  3.08956653e-03  2.95454070e-05
 -5.99709937e-06  1.81219659e-06  2.88234650e-05 -9.98050495e-06
 -2.48074099e-05 -1.53282104e-05  5.73689451e-06  4.23212251e-05
  3.47620590e-03 -1.90255729e-05 -6.77514648e-08 -2.11600482e-05
 -8.10927405e-06  7.31780557e-05  1.55463674e-05 -1.89688855e-05
  4.92338714e-05  3.16587983e-05  1.71973243e-05 -8.21965132e-06
  2.22660936e-06 -2.3297

[ 2.90937374e-05  3.46954547e-03  3.48120544e-03 -1.20060512e-05
  6.16176131e-06 -1.88255198e-05  1.27496343e-02  1.25521781e-05
  4.05962357e-06 -4.78367325e-05  5.60190430e-05  3.45949637e-03
 -2.34299143e-05  1.26780789e-05 -2.05185784e-05 -6.44882304e-05
  6.93175479e-03 -2.24220042e-05  1.05909800e-06  1.03538740e-05
 -1.82300215e-05  6.55888362e-05  3.07463905e-05  5.65275787e-06
  4.53251987e-05 -6.31483095e-06  3.60320132e-05 -7.13675558e-06
  7.34244054e-06 -6.09213578e-06 -4.29727865e-07 -3.57120633e-06]
[-4.46997369e-05  3.42266519e-03  3.48227965e-03 -3.02224548e-05
  7.68128811e-06 -2.11506273e-05  1.26424501e-02  7.02125629e-05
 -5.65662808e-06 -4.17034820e-05  5.13546170e-07  3.47736440e-03
 -2.89387287e-05  2.94771750e-05 -7.12967360e-06 -5.54950560e-06
  6.95669309e-03  2.01682158e-05  3.04520345e-06  1.49496060e-05
 -1.35629903e-05  7.24830278e-05 -5.81897277e-06  2.02726018e-05
  4.78074445e-05  8.89737272e-06  1.49996276e-05  1.05320675e-05
  2.73671055e-05  1.7580

...

[ 2.66433333e-04  5.47788524e-03  1.30858335e-02  2.54636595e-04
 -2.78642400e-05  3.01956308e-02  2.65570637e-04  1.91323184e-02
  4.12728574e-03  1.47391785e-02  3.49989828e-05  5.82812342e-02
 -1.78193845e-05 -6.41185297e-06 -4.97348755e-05 -1.74466905e-05
  5.32204891e-03 -3.64882427e-05 -5.67217334e-06  2.22796461e-03
  4.28856736e-05  3.08812043e-02 -1.08623565e-05  1.35442107e-02
  3.13044067e-05  1.22468412e-05  9.54866201e-06 -1.71670938e-05
  4.83365923e-05  3.75392258e-05  1.56028643e-05  9.96210414e-06]
[ 2.41475760e-04  5.47686023e-03  1.30626639e-02  3.13879355e-04
  1.51762169e-05  3.01357685e-02  2.65544894e-04  1.90565132e-02
  4.18379965e-03  1.47454399e-02  5.13292281e-05  5.82024410e-02
 -1.22698151e-05 -1.45408318e-05 -6.05648535e-05  1.37545444e-05
  5.33655303e-03  1.76311893e-05 -2.82102485e-05  2.25068084e-03
  3.69219573e-05  3.08232581e-02  9.95798774e-06  1.35426671e-02
  1.88708167e-05 -1.74699831e-05 -8.65551497e-06  9.34948702e-06
  2.74207161e-05  4.8584

[ 2.63566271e-04  5.42404890e-03  1.22537366e-02  2.86178121e-04
 -1.63867529e-05  2.83158993e-02  2.99766515e-04  1.78423390e-02
  4.12198458e-03  1.43266651e-02  1.42838308e-05  5.64148293e-02
 -1.05098830e-05  1.16576783e-05  2.05541693e-05 -2.99092526e-05
  5.32201879e-03 -1.18245282e-05 -4.83391058e-06  2.29172408e-03
  2.16292868e-05  3.04629734e-02  1.48272343e-05  1.35389630e-02
  8.00300351e-06 -2.76635208e-05 -2.41603804e-05  3.38174225e-06
  8.88142586e-06  9.40260820e-06  1.36085102e-05  7.32910440e-06]
[ 2.67049026e-04  5.40267165e-03  1.22712477e-02  2.95580140e-04
  1.86264251e-05  2.83123549e-02  2.26822584e-04  1.78898229e-02
  4.15989730e-03  1.43013889e-02  3.31399663e-05  5.64130552e-02
 -3.08531599e-05  1.38292584e-05 -3.47379405e-06 -4.07944960e-05
  5.33431406e-03  4.33006991e-05  1.10662973e-05  2.26374235e-03
  5.07131684e-05  3.03939770e-02  1.52573456e-05  1.35344904e-02
 -1.52792157e-05 -1.31772770e-05 -2.85475692e-05  1.46569222e-05
  8.09915716e-05  6.7481

[ 2.39505150e-04  5.38285351e-03  1.21394411e-02  2.89126851e-04
  1.39821862e-05  2.79874496e-02  2.77475939e-04  1.62922253e-02
  4.18991096e-03  1.34754239e-02  2.75150973e-05  5.48393182e-02
  2.65720360e-06  4.13202307e-05 -3.16559839e-05 -2.76884596e-05
  5.30436934e-03  1.78713667e-05 -3.15455194e-05  2.22800213e-03
 -9.82626914e-06  3.54498893e-02 -4.57592222e-06  1.35692568e-02
  8.47304570e-06 -4.89419901e-05  1.11527121e-05  4.17811715e-05
  2.83846374e-05 -1.29018808e-05  1.49569661e-05  3.44787802e-05]
[ 2.63168375e-04  5.42043039e-03  1.22010139e-02  3.28422655e-04
 -2.79922398e-05  2.79839550e-02  3.28144427e-04  1.62198603e-02
  4.14862956e-03  1.34652219e-02 -3.66301268e-05  5.48756399e-02
 -3.41054666e-05 -3.64026919e-06  1.50365517e-06 -1.60673263e-05
  5.34254572e-03  9.64146397e-07 -4.71343100e-05  2.20489604e-03
  2.04743453e-05  3.55371866e-02  2.42631707e-05  1.35383798e-02
  5.31679243e-06 -7.90311666e-06  2.55322751e-05  1.96390269e-05
  2.34345400e-05 -5.2973

[ 2.57088037e-04  5.29638762e-03  1.17743105e-02  3.08011239e-04
  1.76932925e-05  3.02405657e-02  2.83074831e-04  1.50189474e-02
  4.16820772e-03  1.26484265e-02  5.86618302e-05  5.68685544e-02
 -7.31299886e-06 -2.29716199e-05 -2.36701765e-05 -2.08781982e-05
  5.29006161e-03  7.08759488e-06  1.84228472e-05  2.24087257e-03
 -1.36089791e-05  3.46034902e-02  1.66614799e-05  1.35575472e-02
  5.24730818e-05 -2.07543602e-05  3.96062478e-05  1.80376160e-05
  2.22776381e-05 -1.08649244e-05 -2.27821848e-05  1.82830180e-05]
[ 2.50056503e-04  5.31145555e-03  1.17595831e-02  3.30802781e-04
 -1.70679801e-07  3.02306885e-02  2.35405068e-04  1.50507316e-02
  4.15120103e-03  1.26699924e-02  2.02955596e-05  5.68644421e-02
 -1.13632487e-05  1.21243810e-05 -7.23145526e-06  9.42605772e-06
  5.32655878e-03  7.68846928e-06 -2.31671461e-05  2.24234940e-03
 -2.47690235e-05  3.45835204e-02  3.35532672e-05  1.35429474e-02
  1.49523024e-05  2.11264857e-06  1.20067862e-05  1.29269997e-05
  3.71365244e-05  1.4260

[ 2.43246820e-04  5.20120292e-03  1.14600892e-02  3.05151700e-04
  7.14132782e-06  2.92991679e-02  2.68581925e-04  1.39358825e-02
  4.10931296e-03  1.21102996e-02  1.85854013e-05  5.52866295e-02
 -3.45980936e-05  8.14960682e-07 -6.25204247e-05  2.72801044e-05
  5.27761148e-03  3.72214480e-06  1.98492866e-05  2.25029316e-03
  1.64714258e-06  3.30674778e-02 -8.80380733e-06  1.35745214e-02
  5.99531292e-05 -7.52234161e-06  1.94644710e-05 -2.06729435e-05
  1.60479069e-05  1.15744544e-05 -1.47946729e-05  2.25880536e-05]
[ 2.47254090e-04  5.20259211e-03  1.13874111e-02  2.81744164e-04
  2.08353553e-05  2.93854600e-02  2.54957834e-04  1.39380775e-02
  4.10942674e-03  1.21228978e-02  3.86444787e-05  5.52727093e-02
 -1.49413659e-06  2.97889430e-05 -4.19082681e-05  1.68489604e-05
  5.34371335e-03  3.30009985e-05  2.88067870e-05  2.23347642e-03
  4.92473861e-06  3.31029017e-02  3.91361892e-06  1.35408275e-02
  9.14432164e-06  3.95768154e-05  1.88977283e-05  4.94518345e-06
  1.06994884e-04 -1.9293

In [ ]:
# Plot the performance
N_moves_save = pd.DataFrame(N_moves_save, columns = ['N_moves'])
N_moves_save['N_moves'] = N_moves_save['N_moves'].ewm(span=100, adjust=False).mean()


plt.plot(N_moves_save['N_moves'])
plt.xlabel('Episodes')
plt.ylabel('Number of Steps until Done')
plt.title('Average number of steps until Done per Episode')
plt.show()

R_save = pd.DataFrame(R_save, columns = ['R_save'])
R_save['R_save'] = R_save['R_save'].ewm(span=100, adjust=False).mean()

plt.plot(R_save)
plt.xlabel('Episodes')
plt.ylabel('Reward')
plt.title('Average Rewards per Episode')
plt.show()

In [13]:
# Q -learning

for n in range(N_episodes):
    S,X,allowed_a=env.Initialise_game()
    epsilon_f = epsilon_0 / (1 + beta * n)   ## DECAYING EPSILON
    Done=0                                   ## SET DONE TO ZERO (BEGINNING OF THE EPISODE)
    i = 1                                    ## COUNTER FOR NUMBER OF ACTIONS
    
  
    
    while (Done==0 and i<50):                           ## START THE EPISODE
       
        Qvalues = ComputeQvalues(W1, W2, bias_W1, bias_W2, X, activfunction)  
        a=EpsilonGreedy_Policy(Qvalues,epsilon_f, allowed_a)
        S_next, X_next,allowed_a_next,R,Done=env.OneStep(a)
        
        ## THE EPISODE HAS ENDED, UPDATE...BE CAREFUL, THIS IS THE LAST STEP OF THE EPISODE
        if Done==1:
            R_save[n,]=np.copy(R)
            print(i)
            N_moves_save[n,]=i
            print(N_moves_save[n,])
            
            delta=R-Qvalues[a]
            H = np.matmul(W1,X)+bias_W1
            W2[a,:]=W2[a,:]+eta*delta*H
            
            delta =  W2[a,:].reshape(200, 1)*X.reshape(1, 58)
            W1[:,:]=W1[:,:]+ eta*delta
        
            
            ## TO DO: update biases 
            break
       
  
        
        
        # IF THE EPISODE IS NOT OVER...
        else:
            
            Qvalues1=ComputeQvalues(W1, W2, bias_W1, bias_W2, X_next, activfunction)
            a1=EpsilonGreedy_Policy(Qvalues1,0, allowed_a_next)

            # Compute the delta
            delta=R+gamma*Qvalues1[a1]-Qvalues[a]

            # Update the weights
            H = np.matmul(W1,X)+bias_W1
            W2[a,:]=W2[a,:]+eta*delta*H
            
            delta =  W2[a,:].reshape(200, 1)*X.reshape(1, 58)
            W1[:,:]=W1[:,:]+ eta*delta
            
        # NEXT STATE AND CO. BECOME ACTUAL STATE...     
        S=np.copy(S_next)
        X=np.copy(X_next)
        allowed_a = np.copy(allowed_a_next)
       

        i += 1  # UPDATE COUNTER FOR NUMBER OF ACTIONS



5
[5.]
3
[3.]
1
[1.]
28
[28.]
10
[10.]


C:\Users\adria\AppData\Local\Temp\ipykernel_59400\4002628119.py:11: RuntimeWarning: overflow encountered in matmul
  Qvalues = np.matmul(W2,X1)+bias_W2
C:\Users\adria\AppData\Local\Temp\ipykernel_59400\3634133120.py:53: RuntimeWarning: invalid value encountered in multiply
  delta =  W2[a,:].reshape(200, 1)*X.reshape(1, 58)
C:\Users\adria\AppData\Local\Temp\ipykernel_59400\4002628119.py:5: RuntimeWarning: invalid value encountered in matmul
  H1 = np.matmul(W1,X)+bias_W1 ## make sure that bias_W1 does not need to be transposed
C:\Users\adria\AppData\Local\Temp\ipykernel_59400\3634133120.py:27: RuntimeWarning: invalid value encountered in matmul
  H = np.matmul(W1,X)+bias_W1


27
[27.]
1
[1.]
18
[18.]
37
[37.]
5
[5.]
5
[5.]
2
[2.]
37
[37.]
5
[5.]
3
[3.]
13
[13.]
14
[14.]
12
[12.]
14
[14.]
1
[1.]
9
[9.]
14
[14.]
1
[1.]
16
[16.]
11
[11.]
19
[19.]
22
[22.]
1
[1.]
21
[21.]
1
[1.]
15
[15.]
19
[19.]
3
[3.]
6
[6.]
1
[1.]
15
[15.]
7
[7.]
14
[14.]
1
[1.]
24
[24.]
36
[36.]
1
[1.]
3
[3.]
15
[15.]
30
[30.]
3
[3.]
7
[7.]
7
[7.]
27
[27.]
1
[1.]
34
[34.]
15
[15.]
15
[15.]
6
[6.]
27
[27.]
1
[1.]
1
[1.]
19
[19.]
31
[31.]
10
[10.]
1
[1.]
1
[1.]
1
[1.]
1
[1.]
45
[45.]
8
[8.]
13
[13.]
21
[21.]
17
[17.]
3
[3.]
19
[19.]
2
[2.]
22
[22.]
11
[11.]
12
[12.]
25
[25.]
12
[12.]
1
[1.]
10
[10.]
10
[10.]
1
[1.]
19
[19.]
15
[15.]
35
[35.]
24
[24.]
1
[1.]
10
[10.]
12
[12.]
4
[4.]
1
[1.]
7
[7.]
7
[7.]
31
[31.]
12
[12.]
7
[7.]
14
[14.]
5
[5.]
3
[3.]
1
[1.]
3
[3.]
45
[45.]
11
[11.]
18
[18.]
3
[3.]
6
[6.]
35
[35.]
2
[2.]
2
[2.]
16
[16.]
22
[22.]
2
[2.]
19
[19.]
4
[4.]
10
[10.]
21
[21.]
3
[3.]
3
[3.]
4
[4.]
9
[9.]
30
[30.]
1
[1.]
1
[1.]
14
[14.]
15
[15.]
1
[1.]
12
[12.]
4
[4.]
1
[1.]
3
[3.]
1
[1